.venv (Python 3.10.12) riavviato

In [ ]:
# Constants
MODEL_PATH = "huggingface/CodeBERTa-language-id"
#! pip install transformers, keybert, bertviz

In [ ]:
# Loading the model and tokenizer
from transformers import RobertaTokenizer, RobertaForSequenceClassification

from transformers import TextClassificationPipeline

model = RobertaForSequenceClassification.from_pretrained(MODEL_PATH, output_attentions=True)
tokenizer = RobertaTokenizer.from_pretrained(MODEL_PATH)

pipeline = TextClassificationPipeline(
    model=model,
    tokenizer=tokenizer
)

Some weights of the model checkpoint at huggingface/CodeBERTa-language-id were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Device set to use cpu


In [ ]:
# Base Testing

code_to_test = """
import mod189 from './mod189';
var value=mod189+1;
export default value;
"""

# not working
# inputs = tokenizer(code_to_test)
# print(inputs["input_ids"])
# output = model(inputs)[0]
# language_id = output.argmax()
# print(language_id)

print(pipeline(code_to_test))

RobertaSdpaSelfAttention is used but `torch.nn.functional.scaled_dot_product_attention` does not support non-absolute `position_embedding_type` or `output_attentions=True` or `head_mask`. Falling back to the manual attention implementation, but specifying the manual implementation will be required from Transformers version v5.0.0 onwards. This warning can be removed using the argument `attn_implementation="eager"` when loading the model.


[{'label': 'javascript', 'score': 0.9429981708526611}]


In [ ]:
# trying keyBert

from keybert import KeyBERT
kb_model = KeyBERT(model=model)

kb_model.extract_keywords(code_to_test, highlight=True)

import mod189 from mod189 var value mod189 export default value

[('import', 0.4491),
 ('export', 0.4411),
 ('mod189', 0.4304),
 ('value', 0.2084),
 ('default', 0.0984)]

In [ ]:
# trying Bertviz

from bertviz import head_view, model_view, neuron_view

inputs = tokenizer.encode(code_to_test, return_tensors='pt')
outputs = model(inputs)
attention = outputs[-1]
tokens = tokenizer.convert_ids_to_tokens(inputs[0])
print(tokenizer.decode(inputs[0]))


head_view(attention, tokens)
model_view(attention, tokens)

# neuron view is not working (new(): str type not accepted for attention number)
# neuron_view.show(model=model,model_type="bert", tokenizer=tokenizer, sentence_a=code_to_test)

<s>
import mod189 from './mod189';
var value=mod189+1;
export default value;
</s>


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
# Trying LIME
import lime, torch
from lime.lime_text import LimeTextExplainer
class_names = [
    "go",
    "java",
    "javascript",
    "php",
    "python",
    "ruby",
]

def prediction(texts):
    outputs = model(**tokenizer(texts, return_tensors="pt", padding=True))
    tensor_logits = outputs[0]
    # print(tensor_logits)
    probs = torch.nn.functional.softmax(tensor_logits).detach().numpy()
    # print(probs)
    return probs

# print(tokenizer(code_to_test, return_tensors='pt', padding=True))

explainer = LimeTextExplainer(class_names=class_names)

explaination = explainer.explain_instance(code_to_test, prediction, num_features=20, num_samples=10, top_labels=1)

# print(explaination.available_labels())
explaination.show_in_notebook(text=code_to_test)

<ipython-input-6-55e7cf59b09e>:18: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  probs = torch.nn.functional.softmax(tensor_logits).detach().numpy()
